In [1]:
import pandas as pd
import numpy as np
import re
from datetime import datetime
from dateutil import parser
import matplotlib.pyplot as plt
import pymysql

In [2]:
path = r"D:\Percia_MTech\GUVI\python\Projects\amazon_sales\amazon_data\amazon_india_2020.csv"
df = pd.read_csv(path)
df

transaction_id  order_date         customer_id   product_id  \
0           TXN_2020_00000001  2020-01-19  CUST_2020_00001031  PROD_000402   
1           TXN_2020_00000002  2020-01-19  CUST_2018_00013266  PROD_000486   
2           TXN_2020_00000003  2020-01-17  CUST_2020_00001673  PROD_000278   
3           TXN_2020_00000004  2020-01-25  CUST_2020_00026212  PROD_000245   
4           TXN_2020_00000005  2020-01-01  CUST_2015_00009980  PROD_000765   
...                       ...         ...                 ...          ...   
143710  TXN_2020_00080175_DUP  2020-08-14  CUST_2020_00007573  PROD_001743   
143711  TXN_2020_00010237_DUP  2020-01-18  CUST_2016_00002366  PROD_000304   
143712  TXN_2020_00038556_DUP  2020-04-23  CUST_2020_00045892  PROD_000255   
143713  TXN_2020_00034749_DUP  2020-04-16  CUST_2020_00023707  PROD_001531   
143714  TXN_2020_00044212_DUP  2020-05-08  CUST_2018_00028657  PROD_000443   

                            product_name     category  subcategory    brand  \
0              Xiaomi Poco F1 128GB Blue  Electronics  Smartphones   Xiaomi   
1             Apple iPhone 11 128GB Blue  Electronics  Smartphones    Apple   
2             Xiaomi Redmi 4A 16GB White  Electronics  Smartphones   Xiaomi   
3          Samsung Galaxy S8+ 32GB Black  Electronics  Smartphones  Samsung   
4                    Vivo V20 64GB Black  Electronics  Smartphones     Vivo   
...                                  ...          ...          ...      ...   
143710  Realme Galaxy Tab 8GB RAM Silver  Electronics      Tablets   Realme   
143711                Vivo V7+ 32GB Blue  Electronics  Smartphones     Vivo   
143712  Samsung Galaxy J7 Max 32GB Black  Electronics  Smartphones  Samsung   
143713          HP Gaming 8GB RAM Silver  Electronics      Laptops       HP   
143714              Vivo V11 128GB White  Electronics  Smartphones     Vivo   

       original_price_inr  discount_percent  ...  is_festival_sale  \
0                36202.67              7.11  ...             False   
1               165163.92              0.00  ...             False   
2                32906.94              0.00  ...             False   
3               136675.37             45.87  ...              True   
4                30041.81              0.00  ...             False   
...                   ...               ...  ...               ...   
143710           75266.67              0.00  ...             False   
143711           34469.39              0.00  ...             False   
143712           34026.05              0.00  ...             False   
143713          136596.96              0.00  ...             False   
143714           49003.32             33.74  ...              True   

            festival_name  customer_rating  return_status  order_month  \
0                     NaN              4.5      Cancelled            1   
1                     NaN              NaN       Returned            1   
2                     NaN              5.0      Delivered            1   
3       Republic Day Sale              4.5      Delivered            1   
4                     NaN              4.0      Delivered            1   
...                   ...              ...            ...          ...   
143710                NaN              4.0       Returned            8   
143711                NaN              3.5       Returned            1   
143712                NaN              NaN      Delivered            4   
143713                NaN              4.0      Delivered            4   
143714        Summer Sale              NaN      Delivered            5   

       order_year order_quarter product_weight_kg is_prime_eligible  \
0            2020             1              0.19             False   
1            2020             1              0.19              True   
2            2020             1              0.21              True   
3            2020             1              0.23              True   
4            2020             1             

In [3]:
df.head()

transaction_id  order_date         customer_id   product_id  \
0  TXN_2020_00000001  2020-01-19  CUST_2020_00001031  PROD_000402   
1  TXN_2020_00000002  2020-01-19  CUST_2018_00013266  PROD_000486   
2  TXN_2020_00000003  2020-01-17  CUST_2020_00001673  PROD_000278   
3  TXN_2020_00000004  2020-01-25  CUST_2020_00026212  PROD_000245   
4  TXN_2020_00000005  2020-01-01  CUST_2015_00009980  PROD_000765   

                    product_name     category  subcategory    brand  \
0      Xiaomi Poco F1 128GB Blue  Electronics  Smartphones   Xiaomi   
1     Apple iPhone 11 128GB Blue  Electronics  Smartphones    Apple   
2     Xiaomi Redmi 4A 16GB White  Electronics  Smartphones   Xiaomi   
3  Samsung Galaxy S8+ 32GB Black  Electronics  Smartphones  Samsung   
4            Vivo V20 64GB Black  Electronics  Smartphones     Vivo   

  original_price_inr  discount_percent  ...  is_festival_sale  \
0           36202.67              7.11  ...             False   
1          165163.92              0.00  ...             False   
2           32906.94              0.00  ...             False   
3          136675.37             45.87  ...              True   
4           30041.81              0.00  ...             False   

       festival_name  customer_rating  return_status  order_month order_year  \
0                NaN              4.5      Cancelled            1       2020   
1                NaN              NaN       Returned            1       2020   
2                NaN              5.0      Delivered            1       2020   
3  Republic Day Sale              4.5      Delivered            1       2020   
4                NaN              4.0      Delivered            1       2020   

  order_quarter product_weight_kg is_prime_eligible product_rating  
0             1              0.19             False            3.4  
1             1              0.19              True            4.3  
2             1              0.21              True            4.1  
3             1              0.23              True            3.8  
4             1              0.23             False            3.9  

[5 rows x 34 columns]

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 33165 entries, 0 to 33164
Data columns (total 34 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   transaction_id          33165 non-null  object 
 1   order_date              33165 non-null  object 
 2   customer_id             33165 non-null  object 
 3   product_id              33165 non-null  object 
 4   product_name            33165 non-null  object 
 5   category                33165 non-null  object 
 6   subcategory             33165 non-null  object 
 7   brand                   33165 non-null  object 
 8   original_price_inr      33165 non-null  object 
 9   discount_percent        33165 non-null  float64
 10  discounted_price_inr    33165 non-null  float64
 11  quantity                33165 non-null  int64  
 12  subtotal_inr            33165 non-null  float64
 13  delivery_charges        30511 non-null  float64
 14  final_amount_inr        33165 non-null

In [4]:
df.shape

(143715, 34)

In [5]:
df.isna().sum()

transaction_id                0
order_date                    0
customer_id                   0
product_id                    0
product_name                  0
category                      0
subcategory                   0
brand                         0
original_price_inr            0
discount_percent              0
discounted_price_inr          0
quantity                      0
subtotal_inr                  0
delivery_charges          11518
final_amount_inr              0
customer_city                 0
customer_state                0
customer_tier                 0
customer_spending_tier        0
customer_age_group        17244
payment_method                0
delivery_days                 0
delivery_type                 0
is_prime_member               0
is_festival_sale              0
festival_name             99915
customer_rating           43625
return_status                 0
order_month                   0
order_year                    0
order_quarter                 0
product_

# Data Cleaning

# Q1. Order Date Cleaning

In [6]:
# df['order_date'] = pd.to_datetime(df['order_date'], errors='coerce',dayfirst=True)
# df['order_date'] = df['order_date'].dt.strftime('%Y-%m-%d')
# df
def parse_date(date_str):
    try:
        parsed = parser.parse(date_str, dayfirst=True)
        return parsed.strftime('%Y-%m-%d')
    except (ValueError, TypeError):
        return np.nan  # Use NaN for invalid dates

df['order_date'] = df['order_date'].apply(parse_date)

# Q2. Price Cleaning

In [7]:
df['original_price_inr'] = (
    df['original_price_inr']
    .astype(str)
    .str.replace(r'[₹,]', '', regex=True)
    .str.replace(r'(?i)\brs\b', '', regex=True)     
    .str.replace(r'[^\d.]', '', regex=True)         
)
df['original_price_inr'] = pd.to_numeric(df['original_price_inr'], errors='coerce')

# Q3. Customer Ratings Cleaning

In [8]:
def clean_rating(x):
    if pd.isna(x): return None
    x = str(x).lower()
    if "star" in x: return float(x.split()[0])
    if "/" in x: return float(x.split("/")[0])
    return float(x)

df['customer_rating'] = df['customer_rating'].apply(clean_rating)

# Q4. City Name Cleaning

In [9]:
city_map = {"Bangalore":"Bengaluru","Bombay":"Mumbai","New Delhi":"Delhi"}
df['customer_city'] = df['customer_city'].str.title().replace(city_map)

# Q5. Boolean Columns Cleaning

In [10]:
df['is_prime_member']= df['is_prime_member'].astype(str).str.lower().map(
    {"true": True, "yes": True, "1": True, "y": True,
     "false": False, "no": False, "0": False, "n": False}
)
df['is_prime_eligible'] = df['is_prime_eligible'].astype(str).str.lower().map(
    {"true": True, "yes": True, "1": True, "y": True,
     "false": False, "no": False, "0": False, "n": False}
)
df['is_festival_sale'] = df['is_festival_sale'].astype(str).str.lower().map(
    {"true": True, "yes": True, "1": True, "y": True,
     "false": False, "no": False, "0": False, "n": False}
)

# Q6. Product Category Cleaning

In [11]:
df['category'] = (
    df['category'].str.lower()
    .str.replace("electronics & accessories","electronics")
    .str.strip().str.title()
)

# Q7. Delivery Days Cleaning

In [12]:
df['delivery_days'] = (
    df['delivery_days'].astype(str)
    .str.replace("Same Day","0")
    .str.extract(r'(\d+)').astype(float)
)
df = df[(df['delivery_days']>=0) & (df['delivery_days']<=30)]

# Q8. Duplicate Transactions

In [13]:
df = df.drop_duplicates(subset=['customer_id','product_id','order_date','final_amount_inr'])

# Q9. Outlier Prices

In [14]:
q1,q3 = df['original_price_inr'].quantile([0.25,0.75])
iqr = q3-q1
upper = q3+1.5*iqr
df.loc[df['original_price_inr']>upper*10,'original_price_inr'] /= 100

# Q10. Payment Method Cleaning

In [15]:
pm_map = {
    "upi":"UPI","phonepe":"UPI","googlepay":"UPI",
    "credit card":"Credit Card","cc":"Credit Card",
    "cod":"Cash on Delivery","c.o.d":"Cash on Delivery"
}
df['payment_method'] = df['payment_method'].str.lower().replace(pm_map).str.title()

In [16]:
df.isna().sum()

transaction_id                0
order_date                    0
customer_id                   0
product_id                    0
product_name                  0
category                      0
subcategory                   0
brand                         0
original_price_inr            0
discount_percent              0
discounted_price_inr          0
quantity                      0
subtotal_inr                  0
delivery_charges          11415
final_amount_inr              0
customer_city                 0
customer_state                0
customer_tier                 0
customer_spending_tier        0
customer_age_group        17130
payment_method                0
delivery_days                 0
delivery_type                 0
is_prime_member               0
is_festival_sale              0
festival_name             99193
customer_rating           43321
return_status                 0
order_month                   0
order_year                    0
order_quarter                 0
product_

In [17]:
df.duplicated().sum()

np.int64(0)

# Processing missing/null Values

Fill null vlues in delivery_charges column with 0 because most of the values are 0 and it is numerical data

In [18]:
df[['delivery_charges']] = df[['delivery_charges']].fillna(0)

Fill null vlues in custimer_age_group column with the most frequent age group - mode option

In [19]:
df['customer_age_group'] = df['customer_age_group'].fillna(df['customer_age_group'].mode()[0])

Fill null vlues in festival_name column with "No Festival" value

In [20]:
df['festival_name'] = df['festival_name'].fillna("No Festival")

Fill null vlues in customer_rating column with median value

In [21]:
df['customer_rating'] = pd.to_numeric(df['customer_rating'], errors='coerce')

df['customer_rating'] = df['customer_rating'].fillna(df['customer_rating'].median())


In [22]:
df.isna().sum()

transaction_id            0
order_date                0
customer_id               0
product_id                0
product_name              0
category                  0
subcategory               0
brand                     0
original_price_inr        0
discount_percent          0
discounted_price_inr      0
quantity                  0
subtotal_inr              0
delivery_charges          0
final_amount_inr          0
customer_city             0
customer_state            0
customer_tier             0
customer_spending_tier    0
customer_age_group        0
payment_method            0
delivery_days             0
delivery_type             0
is_prime_member           0
is_festival_sale          0
festival_name             0
customer_rating           0
return_status             0
order_month               0
order_year                0
order_quarter             0
product_weight_kg         0
is_prime_eligible         0
product_rating            0
dtype: int64

# Table Creation and Insertion

In [23]:
conn = pymysql.connect(
    host='localhost',
    user='root',
    password='123456',
    database='amazon_sales'
)
cursor = conn.cursor()

cust_qry = """CREATE TABLE if not exists customers (
    customer_id VARCHAR(50) PRIMARY KEY,
    customer_age_group VARCHAR(20),
    customer_city VARCHAR(50),
    customer_state varchar(50),
    customer_tier varchar(50),
    customer_spending_tier varchar(50),
    customer_rating float,
    is_prime_member BOOLEAN,
    created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
)"""
cursor.execute(cust_qry)

prod_qry = """CREATE TABLE if not exists products (
    product_id VARCHAR(50) PRIMARY KEY,
    product_name VARCHAR(255),
    category VARCHAR(100),
    sub_category VARCHAR(100),
    brand VARCHAR(100),
    is_prime_eligible BOOLEAN,
    created_at TIMESTAMP DEFAULT CURRENT_TIMESTAMP
)"""
cursor.execute(prod_qry)

time_qry = """CREATE TABLE if not exists time_dimension (
    id int auto_increment primary key,
    order_date DATE,
    year INT,
    quarter INT,
    month INT,
    month_name VARCHAR(15),
    day INT,
    weekday INT,
    weekday_name VARCHAR(15),
    festival_name VARCHAR(100),
    is_festival BOOLEAN
)"""
cursor.execute(time_qry)

trans_qry = """CREATE TABLE if not exists transactions (
    transaction_id VARCHAR(50) PRIMARY KEY,
    customer_id VARCHAR(50),
    product_id VARCHAR(50),
    order_date DATE,
    quantity INT,
    original_price_inr float,
    discount_percent float,
    final_amount_inr float,
    delivery_charges float,
    delivery_days INT,
    payment_method VARCHAR(50),
    return_status BOOLEAN,
    customer_rating float
)"""
cursor.execute(trans_qry)

# CREATE INDEX idx_txn_date ON transactions(date_id);
# CREATE INDEX idx_txn_customer ON transactions(customer_id);
# CREATE INDEX idx_txn_product ON transactions(product_id);
# CREATE INDEX idx_txn_category ON products(category);
conn.commit()

In [24]:
df_customers = df[['customer_id', 'customer_age_group','customer_city',
                   'customer_state','customer_tier','customer_spending_tier',
                    'customer_rating', 'is_prime_member']].drop_duplicates()

df_products = df[['product_id', 'product_name', 'category', 'subcategory',
                  'brand', 'is_prime_eligible']].drop_duplicates()

df['order_date'] = pd.to_datetime(df['order_date'], errors='coerce')
df_time = pd.DataFrame()
df_time['order_date'] = df['order_date']
df_time['year'] = df['order_year']
df_time['quarter'] = df['order_quarter']
df_time['month'] = df['order_month']
df_time['month_name'] = df['order_date'].dt.month_name()
df_time['day'] = df['order_date'].dt.day
df_time['weekday'] = df['order_date'].dt.weekday
df_time['weekday_name'] = df['order_date'].dt.day_name()
df_time['festival_name'] = df['festival_name']
df_time['is_festival'] = df['is_festival_sale']

df_txn = df[['transaction_id', 'customer_id', 'product_id', 'order_date',
             'quantity', 'original_price_inr', 'discount_percent', 'final_amount_inr',
             'delivery_charges', 'delivery_days', 'payment_method',
             'return_status', 'customer_rating']].copy()


insert_customer = """
INSERT INTO customers (customer_id, customer_age_group, customer_city,customer_state,
customer_tier,customer_spending_tier,customer_rating, is_prime_member)
VALUES (%s, %s, %s, %s, %s, %s, %s, %s)
ON DUPLICATE KEY UPDATE 
customer_age_group=VALUES(customer_age_group),
customer_city=VALUES(customer_city),
is_prime_member=VALUES(is_prime_member)
"""

for row in df_customers.itertuples(index=False):
    cursor.execute(insert_customer, (
        row.customer_id, row.customer_age_group,
        row.customer_city, row.customer_state,
         row.customer_tier, row.customer_spending_tier, 
         row.customer_rating, bool(row.is_prime_member)
    ))

# --- 2. Insert Products ---
insert_product = """
INSERT INTO products (product_id, product_name, category, sub_category, brand, is_prime_eligible)
VALUES (%s, %s, %s, %s, %s, %s)
ON DUPLICATE KEY UPDATE 
product_name=VALUES(product_name),
category=VALUES(category),
sub_category=VALUES(sub_category),
brand=VALUES(brand),
is_prime_eligible=VALUES(is_prime_eligible)
"""

for row in df_products.itertuples(index=False):
    cursor.execute(insert_product, (
        row.product_id, row.product_name, row.category,
        row.subcategory, row.brand, bool(row.is_prime_eligible)
    ))

# --- 3. Insert Time Dimension ---
insert_time = """
INSERT INTO time_dimension (order_date, year, quarter, month, month_name, day, weekday, 
weekday_name, festival_name, is_festival)
VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
ON DUPLICATE KEY UPDATE 
year=VALUES(year),
quarter=VALUES(quarter),
month=VALUES(month),
month_name=VALUES(month_name),
day=VALUES(day),
weekday=VALUES(weekday),
weekday_name=VALUES(weekday_name),
festival_name=VALUES(festival_name),
is_festival=VALUES(is_festival)
"""

for row in df_time.itertuples(index=False):
    cursor.execute(insert_time, (
        row.order_date, int(row.year), int(row.quarter),
        int(row.month), row.month_name, int(row.day),
        int(row.weekday), row.weekday_name,
        row.festival_name, bool(row.is_festival)
    ))

# --- 4. Insert Transactions ---
insert_txn = """
INSERT INTO transactions (transaction_id, customer_id, product_id, order_date, quantity,
                          original_price_inr, discount_percent, final_amount_inr,
                          delivery_charges, delivery_days, payment_method,
                          return_status, customer_rating)
VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
ON DUPLICATE KEY UPDATE 
customer_id=VALUES(customer_id),
product_id=VALUES(product_id),
order_date=VALUES(order_date),
quantity=VALUES(quantity),
original_price_inr=VALUES(original_price_inr),
discount_percent=VALUES(discount_percent),
final_amount_inr=VALUES(final_amount_inr),
delivery_charges=VALUES(delivery_charges),
delivery_days=VALUES(delivery_days),
payment_method=VALUES(payment_method),
return_status=VALUES(return_status),
customer_rating=VALUES(customer_rating)
"""

for row in df_txn.itertuples(index=False):
    cursor.execute(insert_txn, (
        row.transaction_id, row.customer_id, row.product_id, row.order_date,
        int(row.quantity), row.original_price_inr, row.discount_percent,
        row.final_amount_inr, row.delivery_charges,
        int(row.delivery_days), row.payment_method,
        bool(row.return_status), row.customer_rating
    ))

# --- Commit + Close ---
conn.commit()

In [63]:
df.isna().sum()

transaction_id            0
order_date                0
customer_id               0
product_id                0
product_name              0
category                  0
subcategory               0
brand                     0
original_price_inr        0
discount_percent          0
discounted_price_inr      0
quantity                  0
subtotal_inr              0
delivery_charges          0
final_amount_inr          0
customer_city             0
customer_state            0
customer_tier             0
customer_spending_tier    0
customer_age_group        0
payment_method            0
delivery_days             0
delivery_type             0
is_prime_member           0
is_festival_sale          0
festival_name             0
customer_rating           0
return_status             0
order_month               0
order_year                0
order_quarter             0
product_weight_kg         0
is_prime_eligible         0
product_rating            0
dtype: int64

In [22]:
query = "select * from transactions"
cursor.execute(query)
for val in cursor:
    print(val)

('TXN_2015_00000001', 'CUST_2015_00003884', 'PROD_000021', datetime.date(2015, 1, 25), 1, 123614.0, 27.91, 89112.2, 0.0, 6, 'COD', 1, 5.0)
('TXN_2015_00000002', 'CUST_2015_00011709', 'PROD_000055', datetime.date(2015, 5, 1), 1, 54731.9, 0.0, 54731.9, 0.0, 4, 'COD', 1, 4.5)
('TXN_2015_00000003', 'CUST_2015_00004782', 'PROD_000039', datetime.date(2015, 1, 24), 2, 97644.2, 46.93, 103637.0, 0.0, 4, 'COD', 1, 4.5)
('TXN_2015_00000004', 'CUST_2015_00008105', 'PROD_000085', datetime.date(2015, 1, 28), 1, 21947.3, 0.0, 21947.3, 0.0, 4, 'COD', 1, 3.0)
('TXN_2015_00000005', 'CUST_2015_00002955', 'PROD_000055', datetime.date(2015, 1, 31), 2, 54731.9, 0.0, 109464.0, 0.0, 3, 'COD', 1, 4.0)
('TXN_2015_00000006', 'CUST_2015_00006757', 'PROD_001665', datetime.date(2015, 4, 1), 1, 131195.0, 0.0, 131195.0, 0.0, 3, 'Debit Card', 1, 4.5)
('TXN_2015_00000007', 'CUST_2015_00008012', 'PROD_000031', datetime.date(2015, 1, 27), 1, 86987.6, 0.0, 86987.6, 0.0, 4, 'Credit Card', 1, 3.5)
('TXN_2015_00000008', 'CUS